In [57]:
import os
import json
from pprint import pprint

In [120]:
def simplify_entry(raw_path_root, origin, dest, date_str):
    """
    Given an origin, destination, and date, simplifies to just the JSON we care about for that date entry.
    """
    raw_path = os.path.join(raw_path_root, origin, dest, date_str)
    with open(raw_path, "r") as f:
        data = json.load(f)

    aircrafts = {entry["code"]: entry for entry in data["trips"]["data"]["aircraft"]}
    airports = {entry["code"]: entry for entry in data["trips"]["data"]["airport"]}
    carriers = {entry["code"]: entry for entry in data["trips"]["data"]["carrier"]}
    cities = {entry["code"]: entry for entry in data["trips"]["data"]["city"]}
    
    results = []
    for result in data["trips"]["tripOption"]:
        sale_total = result["saleTotal"]
        assert len(result["slice"]) == 1
        trip_slice = result["slice"][0]
        duration_minutes = trip_slice["duration"]

        segments = []
        for segment in trip_slice["segment"]:
            for leg in segment["leg"]:
                segments.append({
                    "flight_carrier": carriers[segment["flight"]["carrier"]]["name"],
                    "flight_number": segment["flight"]["number"],
                    "aircraft_type": aircrafts[leg["aircraft"]]["name"],
                    "arrival_time": leg["arrivalTime"],
                    "departure_time": leg["departureTime"],
                    "destination": leg["destination"],
                    "duration_minutes": leg["duration"],
                    "origin": leg["origin"],
                })

        results.append({
            "duration_minutes": duration_minutes,
            "sale_total": sale_total,
            "cheapest_fare": False,
            "shortest_duration": False,
            "segments": segments,  
        })

    mark_shortest_duration(results)
    mark_cheapest_fare(results)
    
    return results

In [121]:
def mark_cheapest_fare(results):
    cheapest_price = None
    cheapest_entries = []
    for result in results:
        assert result["sale_total"].startswith("USD")
        result_price = float(result["sale_total"][3:])
        if cheapest_price is None:
            cheapest_price = result_price
            cheapest_entries.append(result)
        elif cheapest_price > result_price:
            cheapest_price = result_price
            cheapest_entries = [result]
        elif cheapest_price == result_price:
            cheapest_entries.append(result)
    
    for cheapest_entry in cheapest_entries:
        cheapest_entry["cheapest_fare"] = True

In [122]:
def mark_shortest_duration(results):
    shortest_duration = None
    shortest_entries = []
    for result in results:
        result_duration = result["duration_minutes"]
        if shortest_duration is None:
            shortest_duration = result_duration
            shortest_entries.append(result)
        elif shortest_duration > result_duration:
            shortest_duration = result_duration
            shortest_entries = [result]
        elif shortest_duration == result_duration:
            shortest_entries.append(result)

    for shortest_entry in shortest_entries:
        shortest_entry["shortest_duration"] = True

In [123]:
raw_path_root = "./data/raw"
os.listdir(raw_path_root)
routes = []
for origin in os.listdir(raw_path_root):
    origin_details = {"origin": origin, "destinations": []}
    for dest in os.listdir(os.path.join(raw_path_root, origin)):
        dest_details = {"dest": dest, "departing_dates": []}
        for date_entry in os.listdir(os.path.join(raw_path_root, origin, dest)):
            print("{} -> {}: {}".format(origin, dest, date_entry))
            date_details = {
                "departure_date": os.path.splitext(date_entry)[0],
                "results": simplify_entry(raw_path_root, origin, dest, date_str),
            }
            dest_details["departing_dates"].append(date_details)
        origin_details["destinations"].append(dest_details)
    routes.append(origin_details)
            

JFK -> BOS: 2017_12_26.json
JFK -> BOS: 2017_12_27.json
JFK -> BOS: 2017_12_28.json
JFK -> BOS: 2017_12_29.json
JFK -> BOS: 2017_12_30.json
JFK -> BOS: 2017_12_31.json
JFK -> BOS: 2018_01_01.json
JFK -> BOS: 2018_01_02.json
JFK -> BOS: 2018_01_03.json
JFK -> LHR: 2017_12_26.json
JFK -> LHR: 2017_12_27.json
JFK -> LHR: 2017_12_28.json
JFK -> LHR: 2017_12_29.json
JFK -> LHR: 2017_12_30.json
JFK -> LHR: 2017_12_31.json
JFK -> LHR: 2018_01_01.json
JFK -> LHR: 2018_01_02.json
JFK -> LHR: 2018_01_03.json
JFK -> SFO: 2017_12_26.json
JFK -> SFO: 2017_12_27.json
JFK -> SFO: 2017_12_28.json
JFK -> SFO: 2017_12_29.json
JFK -> SFO: 2017_12_30.json
JFK -> SFO: 2017_12_31.json
JFK -> SFO: 2018_01_01.json
JFK -> SFO: 2018_01_02.json
JFK -> SFO: 2018_01_03.json
SFO -> BOS: 2017_12_26.json
SFO -> BOS: 2017_12_27.json
SFO -> BOS: 2017_12_28.json
SFO -> BOS: 2017_12_29.json
SFO -> BOS: 2017_12_30.json
SFO -> BOS: 2017_12_31.json
SFO -> BOS: 2018_01_01.json
SFO -> BOS: 2018_01_02.json
SFO -> BOS: 2018_01_

In [124]:
pprint(routes)

[{'destinations': [{'departing_dates': [{'departure_date': '2017_12_26',
                                         'results': [{'cheapest_fare': True,
                                                      'duration_minutes': 68,
                                                      'sale_total': u'USD69.20',
                                                      'segments': [{'aircraft_type': u'Embraer RJ-190',
                                                                    'arrival_time': u'2017-12-26T23:48-05:00',
                                                                    'departure_time': u'2017-12-26T22:40-05:00',
                                                                    'destination': u'BOS',
                                                                    'duration_minutes': 68,
                                                                    'flight_carrier': u'Jetblue Airways Corporation',
                                                              

                                                     {'cheapest_fare': False,
                                                      'duration_minutes': 1068,
                                                      'sale_total': u'USD669.90',
                                                      'segments': [{'aircraft_type': u'Airbus A320',
                                                                    'arrival_time': u'2017-12-26T15:19-08:00',
                                                                    'departure_time': u'2017-12-26T11:50-05:00',
                                                                    'destination': u'SFO',
                                                                    'duration_minutes': 389,
                                                                    'flight_carrier': u'Alaska Airlines Inc.',
                                                                    'flight_number': u'1025',
                                              

                                                                   {'aircraft_type': u'Airbus A319',
                                                                    'arrival_time': u'2017-12-26T18:32-08:00',
                                                                    'departure_time': u'2017-12-26T16:40-08:00',
                                                                    'destination': u'SFO',
                                                                    'duration_minutes': 112,
                                                                    'flight_carrier': u'United Airlines, Inc.',
                                                                    'flight_number': u'1272',
                                                                    'origin': u'PDX'},
                                                                   {'aircraft_type': u'Boeing 757',
                                                                    'arrival_time': u'2017-12-27T0

                                                      'segments': [{'aircraft_type': u'Airbus A320',
                                                                    'arrival_time': u'2017-12-26T15:19-08:00',
                                                                    'departure_time': u'2017-12-26T11:50-05:00',
                                                                    'destination': u'SFO',
                                                                    'duration_minutes': 389,
                                                                    'flight_carrier': u'Alaska Airlines Inc.',
                                                                    'flight_number': u'1025',
                                                                    'origin': u'JFK'},
                                                                   {'aircraft_type': u'Boeing 737',
                                                                    'arrival_time': u'2017-12-26T20

                                                                    'destination': u'PDX',
                                                                    'duration_minutes': 386,
                                                                    'flight_carrier': u'Alaska Airlines Inc.',
                                                                    'flight_number': u'479',
                                                                    'origin': u'JFK'},
                                                                   {'aircraft_type': u'Airbus A319',
                                                                    'arrival_time': u'2017-12-26T18:32-08:00',
                                                                    'departure_time': u'2017-12-26T16:40-08:00',
                                                                    'destination': u'SFO',
                                                                    'duration_minutes': 112,
                

...

                                                                    'departure_time': u'2017-12-26T08:40-08:00',
                                                                    'destination': u'ORD',
                                                                    'duration_minutes': 250,
                                                                    'flight_carrier': u'Deutsche Lufthansa AG',
                                                                    'flight_number': u'7785',
                                                                    'origin': u'SFO'},
                                                                   {'aircraft_type': u'Boeing 767',
                                                                    'arrival_time': u'2017-12-27T06:40+00:00',
                                                                    'departure_time': u'2017-12-26T16:55-06:00',
                                                                    'destination': u'L

                                                                    'origin': u'SFO'},
                                                                   {'aircraft_type': u'Boeing 787',
                                                                    'arrival_time': u'2017-12-27T10:55+00:00',
                                                                    'departure_time': u'2017-12-26T17:25-08:00',
                                                                    'destination': u'LHR',
                                                                    'duration_minutes': 570,
                                                                    'flight_carrier': u'Virgin Atlantic Airways Limited',
                                                                    'flight_number': u'106',
                                                                    'origin': u'SEA'}],
                                                      'shortest_duration': False},
                   

                                                      'shortest_duration': False},
                                                     {'cheapest_fare': False,
                                                      'duration_minutes': 940,
                                                      'sale_total': u'USD948.07',
                                                      'segments': [{'aircraft_type': u'Airbus A330',
                                                                    'arrival_time': u'2017-12-27T11:45+00:00',
                                                                    'departure_time': u'2017-12-26T17:35-08:00',
                                                                    'destination': u'DUB',
                                                                    'duration_minutes': 610,
                                                                    'flight_carrier': u'Aer Lingus Limited',
                                                            

                                                                    'duration_minutes': 332,
                                                                    'flight_carrier': u'United Airlines, Inc.',
                                                                    'flight_number': u'414',
                                                                    'origin': u'SFO'},
                                                                   {'aircraft_type': u'Boeing 767',
                                                                    'arrival_time': u'2017-12-27T06:55+00:00',
                                                                    'departure_time': u'2017-12-26T18:50-05:00',
                                                                    'destination': u'LHR',
                                                                    'duration_minutes': 425,
                                                                    'flight_carrier': u'United Airlines, In

                                                                    'duration_minutes': 465,
                                                                    'flight_carrier': u'Deutsche Lufthansa AG',
                                                                    'flight_number': u'9357',
                                                                    'origin': u'ORD'}],
                                                      'shortest_duration': False},
                                                     {'cheapest_fare': False,
                                                      'duration_minutes': 780,
                                                      'sale_total': u'USD2065.10',
                                                      'segments': [{'aircraft_type': u'Boeing 757',
                                                                    'arrival_time': u'2017-12-26T20:14-06:00',
                                                                    'departure_

In [90]:

origin = "SFO"
dest = "JFK"
date_str = "2017_12_26.json"
results = simplify_entry(raw_path_root, origin, dest, date_str)


In [91]:
results

[{'cheapest_fare': True,
  'duration_minutes': 462,
  'sale_total': u'USD216.80',
  'segments': [{'aircraft_type': u'Airbus A320',
    'arrival_time': u'2017-12-26T20:23-08:00',
    'departure_time': u'2017-12-26T18:55-08:00',
    'destination': u'LAS',
    'duration_minutes': 88,
    'flight_carrier': u'Alaska Airlines Inc.',
    'flight_number': u'1916',
    'origin': u'SFO'},
   {'aircraft_type': u'Airbus A320',
    'arrival_time': u'2017-12-27T05:37-05:00',
    'departure_time': u'2017-12-26T21:50-08:00',
    'destination': u'JFK',
    'duration_minutes': 287,
    'flight_carrier': u'Alaska Airlines Inc.',
    'flight_number': u'1260',
    'origin': u'LAS'}],
  'shortest_duration': False},
 {'cheapest_fare': True,
  'duration_minutes': 411,
  'sale_total': u'USD216.80',
  'segments': [{'aircraft_type': u'Airbus A320',
    'arrival_time': u'2017-12-26T21:14-08:00',
    'departure_time': u'2017-12-26T19:46-08:00',
    'destination': u'LAS',
    'duration_minutes': 88,
    'flight_car

In [67]:
results

[{'duration_minutes': 462,
  'sale_total': u'USD216.80',
  'segments': [{'aircraft_type': u'Airbus A320',
    'arrival_time': u'2017-12-26T20:23-08:00',
    'departure_time': u'2017-12-26T18:55-08:00',
    'destination': u'LAS',
    'duration_minutes': 88,
    'flight_carrier': u'Alaska Airlines Inc.',
    'flight_number': u'1916',
    'origin': u'SFO'},
   {'aircraft_type': u'Airbus A320',
    'arrival_time': u'2017-12-27T05:37-05:00',
    'departure_time': u'2017-12-26T21:50-08:00',
    'destination': u'JFK',
    'duration_minutes': 287,
    'flight_carrier': u'Alaska Airlines Inc.',
    'flight_number': u'1260',
    'origin': u'LAS'}]},
 {'duration_minutes': 411,
  'sale_total': u'USD216.80',
  'segments': [{'aircraft_type': u'Airbus A320',
    'arrival_time': u'2017-12-26T21:14-08:00',
    'departure_time': u'2017-12-26T19:46-08:00',
    'destination': u'LAS',
    'duration_minutes': 88,
    'flight_carrier': u'Alaska Airlines Inc.',
    'flight_number': u'1918',
    'origin': u'SF